# Pass@k curves

In [1]:
import matplotlib.pyplot as plt
from pathlib import Path
from coderm.eval.metrics import get_pass_ks, pass_at_k
from coderm.utils import gunzip_json_read
import numpy as np
from math import comb
import os

def calcEstVar(n, k, c):
    p = c / n
    var = 0
    for i in range(n+1):
        var += comb(n-i, k) * p**i / comb(n, k) * (comb(n-k, i) * (1-p)**(n-i))
    return var - (1-p)**(2*k)

paths_to_results = [
    "../../test_results/ioigpt4omi",
    "../../test_results/ioiplansearch",
    "../../test_results/ioi_ps_sonnet-3-5",
    "../../test_results/basic_prompting_ioi_gpt4o",
    "../../test_results/ioi_ps_sonnet-3-5_long",
    "../../test_results/basic_prompting_ioi_o1-mini"
]

from pathlib import Path
for p in paths_to_results:
    assert Path(p).exists(), f"Path {p} doesn't exist!"

In [2]:
def calc_pass_k(ns, cs, k):
    pass_ks = []
    for n, c in zip(ns, cs):
        pass_ks.append(pass_at_k(n, c, k))
    return pass_ks

def count_ns(items) -> list[int]:
    return [len(item["results"]) for item in items]

def count_cs(items) -> list[int]:
    return [sum(ex["passing"] for ex in item["results"]) for item in items]

def get_max_score(items) -> float:
    score = 0
    for item in items:
        max_score = 0
        for res in item["results"]:
            max_score = max(res["score"], max_score)
        print(f"uniq: {item['prompt'][:10]}, {max_score}")
        score += max_score
    return score

all_pass_ks = {}
for r in (paths_to_results):
    print(f"Reading", r)
    items = gunzip_json_read(r)["items"]
    score = get_max_score(items)
    print(f"{r}: score: {score}")
    # upper_k = max(len(item["results"]) for item in items)
    # print(upper_k)
    # pass_ks = {}
    # ns = count_ns(items)
    # cs = count_cs(items)
    # for k in range(1, upper_k+1):
    #     # pass_ks[k] = np.mean(get_pass_ks(items, k))
    #     pass_ks[k] = np.mean(calc_pass_k(ns, cs, k))
    # all_pass_ks[r] = pass_ks

# all_std = {}
# for r in (paths_to_results + compare):
#     print(f"Reading", r)
#     items = gunzip_json_read(r)["items"]
#     upper_k = len(items[0]["results"])
    
#     vars = []
#     for item in items:
#         single_problem = []
#         for k in range(1, upper_k+1):
#             single_problem.append(calcEstVar(len(items[0]["results"]), k, sum(i["passing"] for i in item["results"])))
#         vars.append(single_problem)

#     vars = np.array(vars)
#     all_std[r] = np.sqrt(np.sum(vars, axis=0) / len(items) ** 2) * 2.5

Reading ../../test_results/ioigpt4omi
uniq: # Tree

Co, 0
uniq: # Nile

Yo, 17
uniq: # Mosaic

, 12
uniq: # Hierogly, 0
../../test_results/ioigpt4omi: score: 29
Reading ../../test_results/ioiplansearch
uniq: # Tree

Co, 0
uniq: # Nile

Yo, 17
uniq: # Mosaic

, 12
uniq: # Hierogly, 0
../../test_results/ioiplansearch: score: 29
Reading ../../test_results/ioi_ps_sonnet-3-5
uniq: # Tree

Co, 0
uniq: # Nile

Yo, 0
uniq: # Mosaic

, 12
uniq: # Hierogly, 0
../../test_results/ioi_ps_sonnet-3-5: score: 12
Reading ../../test_results/basic_prompting_ioi_gpt4o
uniq: # Tree

Co, 0
uniq: # Nile

Yo, 17
uniq: # Mosaic

, 12
uniq: # Hierogly, 0
../../test_results/basic_prompting_ioi_gpt4o: score: 29
Reading ../../test_results/ioi_ps_sonnet-3-5_long
uniq: # Tree

Co, 0
uniq: # Nile

Yo, 0
uniq: # Mosaic

, 12
uniq: # Hierogly, 0
../../test_results/ioi_ps_sonnet-3-5_long: score: 12
Reading ../../test_results/basic_prompting_ioi_o1-mini
uniq: # Tree

Co, 0
uniq: # Nile

Yo, 17
uniq: # Mosaic

, 12
uniq: 

In [4]:
items = gunzip_json_read(paths_to_results[-1])["items"]
items[0]

{'unique_name': '0',
 'prompt': '# Tree\n\nConsider a **tree** consisting of $N$ **vertices**,\n numbered from $0$ to $N-1$.\nVertex $0$ is called the **root**.\nEvery vertex, except for the root, has a single **parent**.\nFor every $i$, such that $1 \\leq i < N$,\n the parent of vertex $i$ is vertex $P[i]$, where $P[i] < i$.\nWe also assume $P[0] = -1$.\n\nFor any vertex $i$ ($0 \\leq i < N$),\n the **subtree** of $i$ is the set of the following vertices:\n * $i$, and\n * any vertex whose parent is $i$, and\n * any vertex whose parent\'s parent is $i$, and\n * any vertex whose parent\'s parent\'s parent is $i$, and\n * etc.\n\nThe picture below shows an example tree consisting of $N = 6$ vertices.\nEach arrow connects a vertex to its parent,\n except for the root, which has no parent.\nThe subtree of vertex $2$ contains vertices $2, 3, 4$ and $5$.\nThe subtree of vertex $0$ contains all $6$ vertices of the tree\n and the subtree of vertex $4$ contains only vertex $4$.\n\n![](subtrees.

In [12]:
from search.exec_utils import run_tests_per_code, run_individual_tests_per_code
from search.dataset_utils import parse_dataset 
problems = parse_dataset("codegenning/F_filterio24", "test")

In [9]:
p = problems[0]
p.subtasks

[{'score': 22, 'test_idxs': [50, 41, 29, 21, 67, 61, 1, 3, 35, 44]},
 {'score': 11,
  'test_idxs': [14, 4, 52, 43, 32, 20, 69, 64, 12, 42, 47, 22, 33, 65]},
 {'score': 0, 'test_idxs': [16]},
 {'score': 7, 'test_idxs': [14, 4, 52, 43, 32, 20, 69, 64]},
 {'score': 18,
  'test_idxs': [58,
   55,
   9,
   6,
   46,
   38,
   26,
   24,
   59,
   5,
   10,
   40,
   51,
   19,
   28,
   62,
   70,
   54,
   11,
   8,
   48,
   39]},
 {'score': 13, 'test_idxs': [58, 55, 9, 6, 46, 38, 26, 24]},
 {'score': 10, 'test_idxs': [17, 56, 57, 7, 13, 45, 49, 23, 31, 15]},
 {'score': 19,
  'test_idxs': [16,
   17,
   56,
   57,
   7,
   13,
   45,
   49,
   23,
   31,
   15,
   58,
   55,
   9,
   6,
   46,
   38,
   26,
   24,
   59,
   5,
   10,
   40,
   51,
   19,
   28,
   62,
   70,
   54,
   11,
   8,
   48,
   39,
   14,
   4,
   52,
   43,
   32,
   20,
   69,
   64,
   12,
   42,
   47,
   22,
   33,
   65,
   50,
   41,
   29,
   21,
   67,
   61,
   1,
   3,
   35,
   44,
   53,
   18,
   3

In [16]:
the_test = [t for i, t in enumerate(p.get_test_private()) if i in {14, 4, 52}]
the_code = 'def main():\n    import sys\n    import threading\n\n    def solve():\n        import sys\n        sys.setrecursionlimit(1 << 25)\n        from collections import defaultdict\n\n        N_and_rest = sys.stdin.read().split()\n        ptr = 0\n\n        N = int(N_and_rest[ptr])\n        ptr += 1\n\n        P = list(map(int, N_and_rest[ptr:ptr + N - 1]))\n        ptr += N - 1\n\n        W = list(map(int, N_and_rest[ptr:ptr + N]))\n        ptr += N\n\n        # Build the tree\n        tree = [[] for _ in range(N)]\n        for child, parent in enumerate(P, start=1):\n            tree[parent].append(child)\n\n        Q = int(N_and_rest[ptr])\n        ptr += 1\n\n        queries = []\n        for _ in range(Q):\n            L = int(N_and_rest[ptr])\n            R = int(N_and_rest[ptr + 1])\n            queries.append((L, R))\n            ptr += 2\n\n        # Precompute post-order traversal\n        post_order = []\n        stack = [(0, False)]\n        while stack:\n            node, visited = stack.pop()\n            if node < 0:\n                post_order.append(~node)\n                continue\n            stack.append((~node, True))\n            for child in tree[node]:\n                stack.append((child, False))\n\n        for L, R in queries:\n            S = [0] * N\n            total_cost = 0\n            for node in post_order:\n                if not tree[node]:  # Leaf node\n                    sum_children = 0\n                else:\n                    sum_children = sum(S[child] for child in tree[node])\n                if sum_children < L:\n                    S[node] = L\n                    total_cost += (L - sum_children) * W[node]\n                elif sum_children > R:\n                    S[node] = R\n                    total_cost += (sum_children - R) * W[node]\n                else:\n                    S[node] = sum_children\n            print(total_cost)\n\n    threading.Thread(target=solve).start()\n\nmain()'
print("nice", len(the_test))
run_individual_tests_per_code([the_code], [the_test], [10], [None], total_num_concurrent=10, num_workers=10, testbank="codegenning/B_i_filterio24_v3")


nice 3
1 AAAAA

AAAA [1]


 33%|███▎      | 1/3 [00:16<00:01,  2.00it/s]

Request rejected, waiting 3 seconds and then retrying... 646ded


 67%|██████▋   | 2/3 [01:03<00:31, 31.55s/it]

Probably finished


[[(False, "errored with 'Timeout'\n"),
  (False, "errored with 'Timeout'\n"),
  (False, "errored with 'Timeout'\n")]]

In [ ]:
# ps_idea4o = []
# ps_idea4omi = []

# # Read and process simple_idea4o
# items_idea4o = gunzip_json_read("p4o_results/simple_idea4o_temp0.5")["items"]
# for item in items_idea4o:
#     trials = []
#     for trial in item["results"]:
#         trials.append(trial["passing"])
#     ps_idea4o.append(sum(trials) / len(trials))

# # Read and process simple_idea4omi
# items_idea4omi = gunzip_json_read("p4o_results/simple_idea4omi_temp0.5")["items"]
# for item in items_idea4omi:
#     trials = []
#     for trial in item["results"]:
#         trials.append(trial["passing"])
#     ps_idea4omi.append(sum(trials) / len(trials))

# # Plot histograms for both distributions
# plt.hist(ps_idea4o, alpha=0.5, label='simple_idea4o')
# plt.hist(ps_idea4omi, alpha=0.5, label='simple_idea4omi')
# plt.legend(loc='upper right')
# plt.xlabel('Problem Solve Probability')
# plt.ylabel('Frequency')
# plt.title('Distribution of Problem Solve Probabilities')
# plt.show()

In [ ]:
# import json
# lol = os.path.join(LOG_DIRECTORY, "results_per_code.json")
# with open(lol, "r") as f:
#     d = json.load(f)
# lens = []
# for p in d:
#     lens.append(len(p["results"]))
# min(lens)
# sum([any(passing["passing"] for passing in res["results"]) for res in d]) / len(d)
# new_d = {"items": d}
# with open(os.path.join(LOG_DIRECTORY, "results_w_item.json"), "w") as f:
#     json.dump(new_d, f)

In [ ]:
plt.figure(figsize=(12, 6))

for label, values in all_pass_ks.items():
    ks = list(values.keys())
    pass_k = list(values.values())
    # std_devs = list(all_std[label])
    linestyle = '--' if any(p in label for p in paths_to_results) and len(compare) > 0 else '-'
    plt.plot(ks, pass_k, label=Path(label), linestyle=linestyle)
    # plt.fill_between(ks, np.array(pass_k) - np.array(std_devs), np.array(pass_k) + np.array(std_devs), alpha=0.2)

plt.xlabel('k')
plt.xscale('log')
plt.ylabel('Pass@k')
plt.title('Pass@k vs k for various methods')
plt.legend(fontsize='small', loc='lower center')
plt.grid(True, which='both', axis='both')  # Add vertical grids
plt.show()

In [ ]:
from one_prompt_models import BasicPromptModel
from base_classes import Problem, Test

spm = BasicPromptModel("gpt-4o-mini")
print(spm.format_problem_to_prompt(Problem("ee", "", [Test(([""], {}), "", None)], None))[0]["content"])
print(spm.format_problem_to_prompt(Problem("ee", "", [Test(([""], {}), "", None)], None))[1]["content"])


In [ ]:
# Generate paths for the 25 result files
idea_temps = [0.2, 0.3, 0.4, 0.5, 0.6]
code_temps = [0.2, 0.3, 0.4, 0.5, 0.6]
heatmap_data = np.zeros((len(idea_temps), len(code_temps)))

sel_k = 90
for i, it in enumerate(idea_temps):
    for j, ct in enumerate(code_temps):
        path = f"sweeps/simpleidea_small_it{it}_ct{ct}"
        if not Path(path).exists():
            pass_ks = 0
        else:
            items = gunzip_json_read(path)["items"]
            pass_ks = np.mean(get_pass_ks(items, sel_k))
        heatmap_data[i, j] = pass_ks
# Plotting the heatmap
plt.figure(figsize=(10, 8))
plt.imshow(heatmap_data, cmap='plasma', origin='lower')
plt.colorbar(label=f'Pass@{sel_k}')
plt.xticks(ticks=np.arange(len(code_temps)), labels=code_temps)
plt.yticks(ticks=np.arange(len(idea_temps)), labels=idea_temps)
plt.xlabel('Code Temperature (ct)')
plt.ylabel('Idea Temperature (it)')
plt.title(f'Pass@{sel_k} Heatmap for Different Temperatures')

# Function to determine text color based on brightness
def get_text_color(value, cmap):
    norm = plt.Normalize(vmin=heatmap_data.min(), vmax=heatmap_data.max())
    rgba = cmap(norm(value))
    brightness = 0.299 * rgba[0] + 0.587 * rgba[1] + 0.114 * rgba[2]
    return 'black' if brightness > 0.5 else 'white'

cmap = plt.get_cmap('plasma')
for i in range(len(idea_temps)):
    for j in range(len(code_temps)):
        text_color = get_text_color(heatmap_data[i, j], cmap)
        plt.text(j, i, f"{heatmap_data[i, j]:.2f}", ha='center', va='center', color=text_color, fontsize=12)
plt.show()

In [ ]:
import matplotlib.pyplot as plt
import numpy as np

datasets = ["mbpp_plus", "human_eval_plus", "livecodebench_lite_v3"]
models = ["gpt-4o-mini", "gpt-4o", "sonnet-3-5", "deepseek-coder"]
similar_types = ["final", "right", "right_wrong", "wrong"]

fig, axes = plt.subplots(len(datasets), len(models), figsize=(20, 15), sharex=True, sharey=True)
fig.suptitle("Comparison of Similar Types Across Datasets and Models", fontsize=16)

for i, dataset in enumerate(datasets):
    for j, model in enumerate(models):
        means = []
        for similar_type in similar_types:
            path = f"../../other_logs/similar_logs/{similar_type}_logs/{dataset}/basic_prompting225_{model}_temp0.9/results.npy"
            data = np.load(path)
            means.append(1 - np.mean(data))
        
        ax = axes[i, j]
        ax.bar(similar_types, means)
        ax.set_title(f"{dataset} - {model}", fontsize=10)
        ax.tick_params(axis='x', rotation=45)
        
        if i == len(datasets) - 1:
            ax.set_xlabel("Similar Types")
        if j == 0:
            ax.set_ylabel("Mean Score")

plt.tight_layout()
plt.show()